# Custom Data 3DCORE

This notebook shows how to use custom data for fitting.

In [1]:
%load_ext autoreload
%autoreload 2


# import packages
from coreweb.methods.offwebutils import extract_row, process_sav, generate_graphstore, get_modelkwargs_ranges, offwebfit, get_eventinfo, update_posfig_offweb, create_movie
from coreweb.dashcore.utils.plotting import check_animation, check_fittingpoints, get_longmove_array
from coreweb.dashcore.utils.utils import load_fit
from coreweb.dashcore.assets.config_sliders import modelslidervars, magslidervars
from coreweb.dashcore.app import update_launch_label#, generate_graphstore
from coreweb.dashcore.pages.Start import update_alert_for_init

import pandas as pd
from IPython.display import display, HTML

import datetime
import urllib
import os

import pickle as p
import numpy as np

import warnings
warnings.filterwarnings('ignore')

In the following code cell, you'll have to add your rawdatas filename. Place the file in the folder 'src/coreweb/dashcore/data/uploaded/' and make sure it contains the required information.

Example:

[(datetime.datetime(2024, 3, 1, 0, 0),  5.95815992, -4.94100904,  1.81143689,  7.95113754, nan, nan, nan, nan, nan, nan, 91419055.62693639, -40959185.8396153 , -6907293.21593887, 0.67122074, -3.94441724, -24.13417982)

 (datetime.datetime(2024, 3, 1, 0, 1),  6.11344147, -4.93733311,  1.66440606,  8.03835583, nan, nan, nan, nan, nan, nan, 91418258.28606315, -40958236.37124682, -6907432.70067896, 0.67121336, -3.94454044, -24.1338707 )

 (datetime.datetime(2024, 3, 1, 0, 2),  6.23410368, -4.75424814,  1.63773108,  8.01020336, nan, nan, nan, nan, nan, nan, 91417460.93920308, -40957286.869865  , -6907572.18215952, 0.67120598, -3.94466364, -24.13356155)

 ...

 (datetime.datetime(2024, 3, 4, 15, 8), -7.1523056 ,  9.15058708, -6.96903658, 13.59475708, nan, nan, nan, nan, nan, nan, 87158410.96876895, -35532740.7860987 , -7587555.46427159, 0.63121531, -4.60882293, -22.17973951)

 (datetime.datetime(2024, 3, 4, 15, 9), -6.79641771,  9.39661884, -6.99923754, 13.57492256, nan, nan, nan, nan, nan, nan, 87157576.0754775 , -35531612.06297739, -7587675.30406619, 0.63120738, -4.60895388, -22.17929512)
 
 (datetime.datetime(2024, 3, 4, 15, 10), -6.12276459,  9.3077507 , -7.93729973, 13.70659161, nan, nan, nan, nan, nan, nan, 87156741.17355627, -35530483.3042728 , -7587795.1395554 , 0.63119946, -4.60908483, -22.1788507 )]


 The function generating the graphstore needs to access:

time = data['time']   --- as datetime objects

bx = data['bx']       --- in nT (RTN)

by = data['by']       --- in nT (RTN)

bz = data['bz']       --- in nT (RTN)

x = data['x']         --- in km (HEEQ)

y = data['y']         --- in km (HEEQ)

z = data['z']         --- in km (HEEQ)

In [12]:
reference_frame = "RTN" # switch to HEEQ if needed 
filename = "examplesyn.p"

filepath = 'src/coreweb/dashcore/data/uploaded/' + filename

cataloglaunchtime = datetime.datetime(2024,3,1,0,0) # replace by correct launchtime

idd = 'ICME_SYN_CUSTOM_' + datetime.datetime.strftime(cataloglaunchtime, '%Y%m%d') + '_01'

eventinfo = get_eventinfo(idd, purelysyn=False, custom=True, loaded = filepath)

graphstore, posstore, _ = generate_graphstore(eventinfo, reference_frame, {})

getting uploaded data
Loading body traces from Data Archive/Helioforecast
Body traces obtained successfully
Mercury traces obtained from Archive/Helioforecast
Venus traces obtained from Archive/Helioforecast
Mars traces obtained from Archive/Helioforecast
Earth traces obtained from Archive/Helioforecast
Body data obtained successfully
Successfully loaded data for SOLO from Data Archive/Helioforecast
Successfully loaded data for PSP from Data Archive/Helioforecast
Successfully loaded data for BEPI from Data Archive/Helioforecast
Successfully loaded data for STEREO-A from Data Archive/Helioforecast


## Plots

Plotting insitu data and positions can be helpful to analyse a given event. Adapting the model and magnetic field parameters influences both 3D shape and insitu magnetic field, as seen in the plots below.

### Set parameters for the model

In [13]:
# launchtime, set hours to impact
launch_formatted = cataloglaunchtime.strftime("%Y-%m-%d %H:%M")
launchlabel = f"Launch Time: {launch_formatted}"

print(launchlabel)

# model parameters

modelstatevars = [0, # Longitude extracted from Donki Catalog, set manually otherwise
                  0, # Latitude extracted from Donki Catalog, set manually otherwise
                  0., # Inclination
                  0.35, # Diameter 1 AU 
                  5., # Aspect Ratio
                  20., # Launch Radius
                  500, # Launch Velocity extracted from Donki Catalog, set manually otherwise
                  1.14, # Expansion Rate
                  1.00, # Background Drag
                  500., # Background Velocity
                  120., # T_Factor
                  1.64, # Magnetic Decay Rate
                  25., # Magnetic Field Strength 1 AU
                  ]

Launch Time: 2024-03-01 00:00


In [14]:
# choose from the following plot options: "Title", "Latitudinal Grid", "Longitudinal Grid","Trajectories","Synthetic Event","Catalog Event","AU axis","Trajectories","Parker Spiral","Catalog Event", "Timer"
plot_options = [
    "Title", 
    "Longitudinal Grid",
    "Trajectories",
    "Synthetic Event",
    "Catalog Event",
    "AU axis",
    "Trajectories",
    "Parker Spiral",
    "Catalog Event", 
    "Timer"]

# choose from the following spacecraft: "SOLO", "PSP", "BEPI", "Wind","STEREO-A", "SYN"
spacecraftoptions =["SYN"]

# choose from the following bodies: "Sun", "Mercury", "Venus","Earth"
bodyoptions = ["Sun"]

view_legend_insitu = True
insitu = True
positions = True
plottheme = 'light-simple' # 'dark', 'light', 'dark-simple', 'light-simple'
currenttimeslider = 25

camera = 'auto' #give r, lon and lat

# this function creates the figure

checkanim = check_animation(None, None, plottheme, graphstore, reference_frame, None, None, None, currenttimeslider, eventinfo, launchlabel, plot_options, spacecraftoptions, bodyoptions, insitu, positions, view_legend_insitu, camera, posstore, *modelstatevars)
#checkanim.write_html("checkanim.html")
checkanim

In [20]:
t_launch = cataloglaunchtime.replace(tzinfo=None) # choose launch time

t_s = datetime.datetime(2024, 3, 1, 22, tzinfo=datetime.timezone.utc) # use start time of event
t_e = datetime.datetime(2024, 3, 2, 4,30, tzinfo=datetime.timezone.utc) # use end time of event if full event arrived already, otherwise use estimated end

# choose arbitrary number of fitting points within the event

t_fit = None # will be set automatically, otherwise set manually

# t_fit =[
#     datetime.datetime(2023, 3, 2, 0, tzinfo=datetime.timezone.utc),
#     datetime.datetime(2023, 3, 2, 2, tzinfo=datetime.timezone.utc),
#     datetime.datetime(2023, 3, 2, 4, tzinfo=datetime.timezone.utc),
# ]

showtitle = True

# this function creates a figure to visually check the previously set points
fig, t_s, t_e, t_fit = check_fittingpoints(graphstore, reference_frame, eventinfo, view_legend_insitu, showtitle, t_fit, t_s, t_e) 
fig

In [31]:
modelstatevar_ranges = [
    int(2**16) # ensemblesize
    ] + [
        [- 20,20], # Longitude (HEEQ)
        [- 20,20], # Latitude (HEEQ)
        [0.,360.], # Inclination
        [0.05,0.35], # Diameter 1 AU 
        [1.,6.], # Aspect Ratio  
        [10.,20.], # Launch Radius
        [500, 1900], # Launch Velocity
        [1.,1.3], # Expansion Rate
        [0.20,3.00], # Background Drag
        [100.,700.], # Background Velocity
        [-250.,250.], # T_Factor
        [1.,2.], # Magnetic Decay Rate
        [5.,20.], # Magnetic Field Strength 1 AU
    ]

modelkwargs = get_modelkwargs_ranges(modelstatevar_ranges)

multiprocessing = True

njobs = 4

itermin = 5
itermax = 8

n_particles = 512

In [32]:
# start the fitting process
filepath = offwebfit(t_launch, eventinfo, graphstore, multiprocessing, t_s, t_e, t_fit, njobs, itermin, itermax, n_particles, modelkwargs)

using noise model psd
Running iteration 0
Initial eps_init =  [1.27752001]
Starting simulations
Multiprocessing is used
515 reached particles                     
Setting new eps: [1.25196961] => [1.07752907]
Step 0 done, 25.95M runs in 226.19 seconds, (total: 00h 03m 46s)
Created directory /Users/hannahruedisser/3DCOREweb/src/coreweb/dashcore/output/ICME_SYN_CUSTOM_20240301_01_HEEQ_202405271200/00.pickle
Saved to /Users/hannahruedisser/3DCOREweb/src/coreweb/dashcore/output/ICME_SYN_CUSTOM_20240301_01_HEEQ_202405271200/00.pickle
Running iteration 1
Starting simulations
Multiprocessing is used


KeyboardInterrupt: 

In [33]:
# in case you don't want to rerun, copypaste path to load:

filepath = '/Users/hannahruedisser/3DCOREweb/src/coreweb/dashcore/output/ICME_SYN_CUSTOM_20240301_01_HEEQ_202405271200/00.pickle'

## Result Analysis

### Show the fitting results

The fitting results can be shown as a scatterplot or in a table.

In [34]:
tablenew, *fitting_values, resdfdic, t0, mean_row, statfig = load_fit(filepath.split('/')[-2], graphstore)

#statfig

Generating and converting ensembles!
512/512


In [35]:
df_mean = pd.DataFrame.from_dict(mean_row)

pd.set_option("display.max_rows", None)

max_col_width = max(len(str(col)) for col in df_mean.columns[2:-1])

for col in df_mean.columns[2:-1]:
    print('{:<{}}{:>20} +/- {:>20}'.format(str(col) + ':', max_col_width + 1, str(df_mean[col][0]), str(df_mean[col][1])))

Longitude:                                  -7.86 +/-                 9.23
Latitude:                                   -1.68 +/-                10.33
Inclination:                               230.46 +/-               127.27
Diameter 1 AU:                               0.19 +/-                 0.05
Aspect Ratio:                                 4.2 +/-                 1.24
Launch Radius:                              15.79 +/-                 2.86
Launch Velocity:                          1649.07 +/-               173.83
T_Factor:                                    7.57 +/-               133.92
Expansion Rate:                              1.15 +/-                 0.09
Magnetic Decay Rate:                         1.47 +/-                 0.29
Magnetic Field Strength 1 AU:               11.28 +/-                 4.06
Background Drag:                             0.36 +/-                 0.17
Background Velocity:                       604.46 +/-                78.38
Number of Twists:        

In [36]:
df = pd.DataFrame.from_dict(resdfdic)

pd.set_option("display.max_rows", None)

# Puts the scrollbar next to the DataFrame
display(HTML("<div style='height: 200px; overflow: auto; width: fit-content'>" +
             df.style.render() +
             "</div>"))

In [37]:
row= df.iloc[df['RMSE Ɛ'].idxmin()] # extract parameters from random row
row

Index                                         98
RMSE Ɛ                                      0.67
Longitude                                  -8.92
Latitude                                   -2.59
Inclination                               354.63
Diameter 1 AU                               0.14
Aspect Ratio                                4.17
Launch Radius                              19.64
Launch Velocity                          1615.01
T_Factor                                   -25.3
Expansion Rate                              1.17
Magnetic Decay Rate                         1.35
Magnetic Field Strength 1 AU               10.87
Background Drag                             0.33
Background Velocity                       604.94
Number of Twists                           -1.42
Launch Time                     2024-03-01 00:00
Name: 98, dtype: object

In [38]:
# read from pickle file
file = open(filepath, "rb")
data = p.load(file)
file.close()
        
ensemble_filepath = filepath.split('.')[0] + '_ensembles.pickle'
with open(ensemble_filepath, 'rb') as ensemble_file:
    ensemble_data = p.load(ensemble_file)  

In [39]:
# this function creates the figure
checkanim_fit = check_animation(None, ensemble_data, plottheme, graphstore, reference_frame, None, None, None, currenttimeslider, eventinfo, launchlabel, plot_options, spacecraftoptions, bodyoptions,  insitu, positions, view_legend_insitu, camera, posstore, *extract_row(row))
#checkanim_fit.write_html("checkanim.html")
checkanim_fit.show()